<a href="https://colab.research.google.com/github/MarwanAhmed20/Lip-Synchronization-with-Wav2Lip-and-GFPGAN/blob/main/Wav2Lip_UI.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#@title <h1>Step1: Setup Wav2Lip</h1>
#@markdown * Install dependency
#@markdown * Download pretrained model
from IPython.display import HTML, clear_output
!rm -rf /content/sample_data
!mkdir /content/sample_data

!git clone https://github.com/ajay-sainy/Wav2Lip-GFPGAN.git
%cd /content/Wav2Lip-GFPGAN
!pip install -r requirements.txt

#download the pretrained model
!wget 'https://www.adrianbulat.com/downloads/python-fan/s3fd-619a316812.pth' -O '/content/Wav2Lip-GFPGAN/Wav2Lip-master/face_detection/detection/sfd/s3fd.pth'
!gdown https://drive.google.com/uc?id=1fQtBSYEyuai9MjBOF8j7zZ4oQ9W2N64q --output '/content/Wav2Lip-GFPGAN/Wav2Lip-master/checkpoints/'

!pip install pydub
!kaggle datasets download -d sergiovirahonda/shape-predictor-68-face-landmarksdat
!unzip shape-predictor-68-face-landmarksdat.zip
!pip install dlib


from IPython.display import HTML
from base64 import b64encode
def showVideo(path):
  mp4 = open(str(path),'rb').read()
  data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
  return HTML("""
  <video width=700 controls>
        <source src="%s" type="video/mp4">
  </video>
  """ % data_url)


from IPython.display import clear_output

clear_output()
print("All set and ready!")

All set and ready!


In [ ]:
#@title Step2: Select an uploading method

import os
import shutil
from google.colab import drive
from google.colab import files
from IPython.display import HTML, clear_output
from base64 import b64encode
import moviepy.editor as mp


def showVideo(file_path):
    """Function to display video in Colab"""
    mp4 = open(file_path,'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
    display(HTML("""
    <video controls width=600>
        <source src="%s" type="video/mp4">
    </video>
    """ % data_url))

def get_video_resolution(video_path):
    """Function to get the resolution of a video"""
    import cv2
    video = cv2.VideoCapture(video_path)
    width = int(video.get(cv2.CAP_PROP_FRAME_WIDTH))
    height = int(video.get(cv2.CAP_PROP_FRAME_HEIGHT))
    return (width, height)

def resize_video(video_path, new_resolution):
    """Function to resize a video"""
    import cv2
    video = cv2.VideoCapture(video_path)
    fourcc = int(video.get(cv2.CAP_PROP_FOURCC))
    fps = video.get(cv2.CAP_PROP_FPS)
    width, height = new_resolution
    output_path = os.path.splitext(video_path)[0] + '_720p.mp4'
    writer = cv2.VideoWriter(output_path, fourcc, fps, (width, height))
    while True:
        success, frame = video.read()
        if not success:
            break
        resized_frame = cv2.resize(frame, new_resolution)
        writer.write(resized_frame)
    video.release()
    writer.release()



#@markdown ### Select an uploading method
upload_method = "Upload" #@param ["Upload", "Custom Path"]


# remove previous input video
if os.path.isfile('/content/sample_data/input_vid.mp4'):
    os.remove('/content/sample_data/input_vid.mp4')

if upload_method == "Upload":

    uploaded = files.upload()
    for filename in uploaded.keys():
        os.rename(filename, '/content/sample_data/input_vid.mp4')
    PATH_TO_YOUR_VIDEO = '/content/sample_data/input_vid.mp4'

elif upload_method == 'Custom Path':
    #@markdown ``Add the full path to your video on your Gdrive `` 👇
    PATH_TO_YOUR_VIDEO = '/content/drive/MyDrive/test.mp4' #@param {type:"string"}
    if not os.path.isfile(PATH_TO_YOUR_VIDEO):
        print("ERROR: File not found!")
        raise SystemExit(0)
#@markdown ___
#@markdown <b> selcet if your video has mouth movement</b>
Freeze_Mouth_Movements = False #@param {type:"boolean"}
#@markdown Note: ``it takes long time``
#@markdown ___
#@markdown <font color="orange">Notes:


#@markdown <font color="orange">. ``Do not upload videos longer than 60 seconds.``

#@markdown <font color="orange">. ``if the result video has two mouthes select Freeze_Mouth_Movements ``

#@markdown ___

video_duration = mp.VideoFileClip(PATH_TO_YOUR_VIDEO).duration
if video_duration > 60:
    print("WARNING: Video duration exceeds 60 seconds. Please upload a shorter video.")
    raise SystemExit(0)

video_resolution = get_video_resolution(PATH_TO_YOUR_VIDEO)
print(f"Video resolution: {video_resolution}")
if video_resolution[0] >= 1920 or video_resolution[1] >= 1080:
    print("Resizing video to 720p...")
    os.system(f"ffmpeg -i {PATH_TO_YOUR_VIDEO} -vf scale=1280:720 /content/sample_data/input_vid.mp4")
    PATH_TO_YOUR_VIDEO = "/content/sample_data/input_vid.mp4"
    print("Video resized to 720p")
else:
    print("No resizing needed")

if upload_method == "Upload":
  clear_output()
  print("Input Video")
  showVideo(PATH_TO_YOUR_VIDEO)
else:
    if os.path.isfile(PATH_TO_YOUR_VIDEO):
        # Check if the source and destination files are the same
        if PATH_TO_YOUR_VIDEO != "/content/sample_data/input_vid.mp4":
            shutil.copyfile(PATH_TO_YOUR_VIDEO, "/content/sample_data/input_vid.mp4")
            print("Video copied to destination.")

        print("Input Video")
        # Display the video from the destination path
        showVideo("/content/sample_data/input_vid.mp4")

if Freeze_Mouth_Movements == True:
  import cv2
  import os

  video_path = '/content/sample_data/input_vid.mp4'

  frames_dir = '/content/extracted_frames'
  os.makedirs(frames_dir, exist_ok=True)

  # Extract frames from the video
  cap = cv2.VideoCapture(video_path)
  frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
  success, frame = cap.read()
  count = 0

  while success:
      frame_filename = os.path.join(frames_dir, f'frame_{count:04d}.png')
      cv2.imwrite(frame_filename, frame)
      success, frame = cap.read()
      count += 1

  cap.release()
  frame_count, frames_dir
  # Download the shape-predictor model for facial landmarks
  !kaggle datasets download -d sergiovirahonda/shape-predictor-68-face-landmarksdat
  !unzip shape-predictor-68-face-landmarksdat.zip
  # Extract landmarks of the face and get the mouth region
  import dlib
  from imutils import face_utils
  import matplotlib.pyplot as plt

  # Load the pre-trained facial landmark predictor
  predictor_path = "/content/shape_predictor_68_face_landmarks.dat"
  predictor = dlib.shape_predictor(predictor_path)

  # Initialize dlib's face detector
  detector = dlib.get_frontal_face_detector()

  # Extracts the mouth region from a given frame using the facial landmark predictor.
  def extract_mouth_region(frame, predictor):

      gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
      rects = detector(gray, 1)

      for rect in rects:
          shape = predictor(gray, rect)
          shape = face_utils.shape_to_np(shape)

          (mStart, mEnd) = face_utils.FACIAL_LANDMARKS_IDXS["mouth"]
          mouth_points = shape[mStart:mEnd]

          x, y, w, h = cv2.boundingRect(mouth_points)
          return (x, y, w, h)

      return None

  # Process each frame to freeze the mouth region during silent audio periods
  modified_frames_dir = 'modified_frames'
  os.makedirs(modified_frames_dir, exist_ok=True)

  # Load the first frame to use as the static mouth image
  first_frame_path = os.path.join(frames_dir, 'frame_0000.png')
  first_frame = cv2.imread(first_frame_path)
  mouth_bbox = extract_mouth_region(first_frame, predictor)

  # Crop the mouth region from the first frame
  x, y, w, h = mouth_bbox
  static_mouth = first_frame[y:y+h, x:x+w]

  # Process each frame
  for frame_filename in sorted(os.listdir(frames_dir)):
      frame_path = os.path.join(frames_dir, frame_filename)
      frame = cv2.imread(frame_path)

      if frame is not None:
          bbox = extract_mouth_region(frame, predictor)

          if bbox is not None:
              x, y, w, h = bbox
              if frame[y:y+h, x:x+w].shape != static_mouth.shape:
                  static_mouth_resized = cv2.resize(static_mouth, (w, h))
                  frame[y:y+h, x:x+w] = static_mouth_resized
              else:
                  frame[y:y+h, x:x+w] = static_mouth

          modified_frame_path = os.path.join(modified_frames_dir, frame_filename)
          cv2.imwrite(modified_frame_path, frame)

  # Convert processed frames back to video
  output_video_path = '/content/sample_data/input_vid.mp4'
  fps = 30  # Set the frames per second for the output video

  frame_files = sorted([os.path.join(modified_frames_dir, f) for f in os.listdir(modified_frames_dir) if f.endswith('.png')])
  frame = cv2.imread(frame_files[0])
  height, width, layers = frame.shape

  fourcc = cv2.VideoWriter_fourcc(*'mp4v')
  video = cv2.VideoWriter(output_video_path, fourcc, fps, (width, height))

  for frame_file in frame_files:
      frame = cv2.imread(frame_file)
      video.write(frame)

  video.release()

Input Video


In [ ]:
#@title STEP3: Select Audio (Upload from local drive or Gdrive)
import os
from IPython.display import Audio
from IPython.core.display import display
from IPython.display import clear_output
upload_method = 'Upload' #@param ['Upload', 'Custom Path']

#remove previous input audio
if os.path.isfile('/content/sample_data/input_audio.wav'):
    os.remove('/content/sample_data/input_audio.wav')

def displayAudio():
  display(Audio('/content/sample_data/input_audio.wav'))


if upload_method == 'Upload':
  from google.colab import files
  uploaded = files.upload()
  for fn in uploaded.keys():
    print('User uploaded file "{name}" with length {length} bytes'.format(
        name=fn, length=len(uploaded[fn])))

  # Consider only the first file
  PATH_TO_YOUR_AUDIO = str(list(uploaded.keys())[0])

  # Load audio with specified sampling rate
  import librosa
  audio, sr = librosa.load(PATH_TO_YOUR_AUDIO, sr=None)

  # Save audio with specified sampling rate
  import soundfile as sf
  sf.write('/content/sample_data/input_audio.wav', audio, sr, format='wav')



elif upload_method == 'Custom Path':
  from google.colab import drive
  drive.mount('/content/drive')
  #@markdown ``Add the full path to your audio on your Gdrive`` 👇
  PATH_TO_YOUR_AUDIO = '/content/drive/MyDrive/test.wav' #@param {type:"string"}

  # Load audio with specified sampling rate
  import librosa
  audio, sr = librosa.load(PATH_TO_YOUR_AUDIO, sr=None)

  # Save audio with specified sampling rate
  import soundfile as sf
  sf.write('/content/sample_data/input_audio.wav', audio, sr, format='wav')



from pydub import AudioSegment
from pydub.silence import detect_nonsilent

# Load your audio file
audio = AudioSegment.from_file('/content/sample_data/input_audio.wav')

# Detect nonsilent chunks in the audio file
nonsilent_chunks = detect_nonsilent(audio, min_silence_len=1000, silence_thresh=audio.dBFS-16)

# If there's at least one nonsilent chunk, trim the audio to that part
if nonsilent_chunks:
    start_trim = nonsilent_chunks[0][0]
    end_trim = nonsilent_chunks[-1][1]
    trimmed_audio = audio[start_trim:end_trim]

    # Save the trimmed audio
    trimmed_audio.export("/content/sample_data/input_audio.wav", format="wav")

clear_output()
displayAudio()


In [ ]:
#@title STEP4: Start Crunching and Preview Output
#@markdown * Perform Lip-sync

base_Path = '/content/Wav2Lip-GFPGAN'
%cd {base_Path}
# Set up paths and variables for the output file
outputPath = base_Path + '/outputs'
output_file_path = base_Path + '/outputs/result.mp4'
wav2lip_folder = 'Wav2Lip-master'
checkpoint_path = 'checkpoints/wav2lip.pth'

if not os.path.exists(outputPath):
  os.makedirs(outputPath)

inputVideoPath = "//content/sample_data/input_vid.mp4"

inputAudioPath = "/content/sample_data/input_audio.wav"

# Delete existing output file before processing, if any
if os.path.exists(output_file_path):
    os.remove(output_file_path)

!cd $wav2lip_folder && python inference.py --checkpoint_path $checkpoint_path --face {inputVideoPath} --audio {inputAudioPath} \
--outfile {output_file_path}

#Preview output video
if os.path.exists(output_file_path):
    clear_output()
    print("Final Video Preview")
    print("Download this video from", output_file_path)
    showVideo(output_file_path)
else:
    print("Processing failed. Output video not found.")